- augmenter la RAM utilisée par SPARK !! : http://www.datastax.com/dev/blog/zen-art-spark-maintenance, http://www.datastax.com/dev/blog/common-spark-troubleshooting : **plus ou moins fait... à ajuster éventuellement**
- faire la table dans cassandra **fait : vérifier que le schéma est correct**
- dropper le poids ** oublié... à faire : changer le schéma de la table dans cqlsh et changer le code de chargement des DataFrame**
- ajouter une colonne date (full timestamp) ** fait **
- insérer fichier par fichier ? charger par batch de fichiers ? ** en test **
- possible de paralleliser ? ** je ne pense pas : idée ? **
- faire un test sur la vitesse de chargement : ** en cours **

----

## Vérification du bon fonctionnement de PySpark

In [1]:
sc.master

u'spark://172.31.31.138:7077'

In [3]:
rdd = sc.parallelize(xrange(10000000), 8)

In [4]:
rdd.getNumPartitions()

8

In [1]:
rdd.cache()

NameError: name 'rdd' is not defined

In [6]:
rdd.map(lambda x: (x % 1000, x)).filter(lambda x : x[0] % 5 == 0).groupByKey().mapValues(list).collect()

[(0,
  [2500000,
   2501000,
   2502000,
   2503000,
   2504000,
   2505000,
   2506000,
   2507000,
   2508000,
   2509000,
   2510000,
   2511000,
   2512000,
   2513000,
   2514000,
   2515000,
   2516000,
   2517000,
   2518000,
   2519000,
   2520000,
   2521000,
   2522000,
   2523000,
   2524000,
   2525000,
   2526000,
   2527000,
   2528000,
   2529000,
   2530000,
   2531000,
   2532000,
   2533000,
   2534000,
   2535000,
   2536000,
   2537000,
   2538000,
   2539000,
   2540000,
   2541000,
   2542000,
   2543000,
   2544000,
   2545000,
   2546000,
   2547000,
   2548000,
   2549000,
   2550000,
   2551000,
   2552000,
   2553000,
   2554000,
   2555000,
   2556000,
   2557000,
   2558000,
   2559000,
   2560000,
   2561000,
   2562000,
   2563000,
   2564000,
   2565000,
   2566000,
   2567000,
   2568000,
   2569000,
   2570000,
   2571000,
   2572000,
   2573000,
   2574000,
   2575000,
   2576000,
   2577000,
   2578000,
   2579000,
   2580000,
   2581000,
   2582000,

In [4]:
rdd

[4, 6]

---

## Chargement des données

In [2]:
from time import time
from pyspark.sql import SQLContext
from boto.s3.connection import S3Connection
import pandas as pd
import re
sql = SQLContext(sc)

On récupère la liste des fichiers

In [3]:
conn = S3Connection()
bucket = conn.get_bucket('telecom-bigdata-2016')
keys = bucket.list('projet/pagecounts')
datafiles = ['s3n://telecom-bigdata-2016/{}'.format(key.name) for key in keys]

In [4]:
print('Il existe {} fichiers.'.format(len(datafiles)))

Il existe 2160 fichiers.


A chaque fichier on associer un jour et une heure :

In [5]:
def to_day_index(month, day):
    '''
    Parameters:
    -----------
    month : between 1 (january 2011) and 3 (march 2011)
    day : between 1 and 31
    Returns:
    --------
    day number starting from 2011'01'01 as 0
    '''
    days_in_month = [31, 28, 31]
    return sum(days_in_month[:month-1]) + (day - 1)    

In [6]:
def to_month_day(day_index):
    '''
    Parameters:
    -----------
    day number starting from 2011'01'01 as 0 (max is 89)
    Returns:
    --------
    month : between 1 (january 2011) and 3 (march 2011)
    day : between 1 and 31
    '''
    if day_index < 31:
        return 1, day_index + 1
    elif day_index < 59:
        return 2, day_index - 30
    else:
        return 3, day_index - 58

In [7]:
def extract_date(datafile):
    '''
    Return day (day 0 = 2011'01-01) and hour (from 0 to 23)
    '''
    rex = re.compile(r'.*pagecounts-(\d{4})(\d{2})(\d{2})-(\d{2}).*')
    s = rex.match(datafile)
    #datetime = '{}-{}-{} {}:00'.format(*(s.group(i) for i in range(1, 5)))
    day = to_day_index(int(s.group(2)), int(s.group(3)))
    hour = int(s.group(4))
    return day, hour

In [8]:
datafiles_datetimes = [(datafile, extract_date(datafile)) for datafile in datafiles]

On parallélise cette liste (on fait 10 partitions puisqu'on a 10 workers):

Le travail de chaque worker est de :
1. charger un fichier (comme ce sont des fichiers zippés, ils ne peuvent pas être lus en parallèle : on utilisera donc pandas qui peut lire rapidement, en excluant une colonne)
2. appliquer les transformations nécessaires : ajouter une colonne *datetime*, retirer la colonne *weight*, retirer les lignes qui ne correspondent pas à un article Wikipedia (i.e. dont le code projet contient '.')
3. répéter 1. et 2. quatre fois (~ 1 Go max d'utilisation pour 4 fichiers, on a de la marge normalement puisque les workers ont 3 Go de RAM allouée) et concaténer le tout dans la même dataframe pandas
4. flatmapper le tout 

**ATTENTION : PENSER A ENLEVER *NROWS=100* POUR LA VERSION FINALE !!!**

In [41]:
def create_df_non_parallel(datafile_datetime):
    '''
    Pandas nous permet de lire rapidement le fichier (on saute directement une colonne).
    Parameters:
    -----------
    datafile_datetime : 2-tuple with the filename and the date time
    '''
    datafile, (day, hour) = datafile_datetime
    df = pd.read_csv(datafile, sep=' ', compression='gzip', engine='c', header=None, 
                     names=['projectcode', 'page', 'views'], usecols=[0, 1, 2], 
                     na_values=None, keep_default_na=False,
                     dtype={'projectcode': pd.np.str, 'page': pd.np.str, 'views': pd.np.int64})
    # on supprime les pages non-wikipedia
    # on supprime les pages avec 1 seule vue (puisqu'on veut le trend, 1 et
    # 0 ce n'est pas très différent)
    df = df[(df.views > 5) & (~ df.projectcode.str.contains('\.'))]
    df['day'] = day
    df['hour'] = hour
    return df.values.tolist()

In [12]:
def create_df(datafile_datetime):
    '''
    Pandas nous permet de lire rapidement le fichier (on saute directement une colonne).
    Parameters:
    -----------
    datafile_datetime : 2-tuple with the filename and the date time
    '''
    datafile, (day, hour) = datafile_datetime
    df = pd.read_csv(datafile, sep=' ', compression='gzip', engine='c', header=None, 
                     names=['projectcode', 'page', 'views'], usecols=[0, 1, 2], 
                     na_values=None, keep_default_na=False,
                     dtype={'projectcode': pd.np.str, 'page': pd.np.str, 'views': pd.np.int64})
    # on supprime les pages non-wikipedia
    # on supprime les pages avec 1 seule vue (puisqu'on veut le trend, 1 et
    # 0 ce n'est pas très différent)
    df = df[(df.views > 5) & (~ df.projectcode.str.contains('\.'))]
    df['day'] = day
    df['hour'] = hour
    return df.values.tolist()

On teste sur 20 fichiers :

Le fichier suivant semble être corrompu

In [48]:
dd = datafiles_datetimes[1967]

In [49]:
dd

('s3n://telecom-bigdata-2016/projet/pagecounts-20110323-230000.gz', (81, 23))

In [ ]:
df = create_df_non_parallel(dd)

On le télécharge sur http://dumps.wikimedia.org/other/pagecounts-raw/2011/2011-03/

In [31]:
!wget http://dumps.wikimedia.org/other/pagecounts-raw/2011/2011-03/pagecounts-20110323-220000.gz

--2016-02-02 09:04:47--  http://dumps.wikimedia.org/other/pagecounts-raw/2011/2011-03/pagecounts-20110323-220000.gz
Resolving dumps.wikimedia.org (dumps.wikimedia.org)... 208.80.154.11, 2620:0:861:1:208:80:154:11
Connecting to dumps.wikimedia.org (dumps.wikimedia.org)|208.80.154.11|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 77682999 (74M) [application/octet-stream]
Saving to: ‘pagecounts-20110323-220000.gz’

100%[======================================>] 77,682,999  2.08MB/s   in 36s    

2016-02-02 09:05:23 (2.04 MB/s) - ‘pagecounts-20110323-220000.gz’ saved [77682999/77682999]



In [32]:
df = pd.read_csv('file:///home/ubuntu/projetnosql/pagecounts-20110323-220000.gz',
                     sep=' ', compression='gzip', engine='c', header=None, 
                     names=['projectcode', 'page', 'views'], usecols=[0, 1, 2], 
                     na_values=None, keep_default_na=False,
                     dtype={'projectcode': pd.np.str, 'page': pd.np.str, 'views': pd.np.int64})

In [98]:
rdd = sc.parallelize(datafiles_datetimes[first:last-1], 10)
rdd2 = rdd.flatMap(create_df)
df = sql.createDataFrame(rdd2, ['projectcode', 'page', 'views', 'day', 'hour'])
df.write.format("org.apache.spark.sql.cassandra").\
    options(table="wikidata", keyspace="projet").\
    save(mode="append")

In [99]:
t1 = time()
total = t1 - t0
m = total // 60
h = m // 60
m = m % 60
s = total % 60

In [100]:
with open("log_time", "a") as f:
    f.write('\n [TEST] Lecture et écritures des fichiers {} à {} en {} heures {} minutes et {} secondes.\n'.
            format(first, last, h, m, s))

---